## Random NN modes

### Fully randomized model

In [1]:
from math import ceil
from random import uniform

from xenonpy.model.nn import Generator1d
from xenonpy.model.nn import wrap

g = Generator1d(290, 1,
                n_neuron=[ceil(uniform(0.8, 1.2) * 290) for n in range(5)],
                layer_func=(wrap.L1.conv(kernel_size=3),),
                batch_normalize=(wrap.L1.batch_norm(),)
               )

ms = g(5, n_models=10, replace=False)  # return generator
m = next(ms)
m

Sequential(
  (0): Layer1d(
    (layer): Conv1d(290, 328, kernel_size=(3,), stride=(1,))
    (batch_nor): BatchNorm1d(328, eps=1e-05, momentum=0.1, affine=True)
    (act_func): ReLU()
  )
  (1): Layer1d(
    (layer): Conv1d(328, 341, kernel_size=(3,), stride=(1,))
    (batch_nor): BatchNorm1d(341, eps=1e-05, momentum=0.1, affine=True)
    (act_func): ReLU()
  )
  (2): Layer1d(
    (layer): Conv1d(341, 332, kernel_size=(3,), stride=(1,))
    (batch_nor): BatchNorm1d(332, eps=1e-05, momentum=0.1, affine=True)
    (act_func): ReLU()
  )
  (3): Layer1d(
    (layer): Conv1d(332, 327, kernel_size=(3,), stride=(1,))
    (batch_nor): BatchNorm1d(327, eps=1e-05, momentum=0.1, affine=True)
    (act_func): ReLU()
  )
  (4): Layer1d(
    (layer): Conv1d(327, 332, kernel_size=(3,), stride=(1,))
    (batch_nor): BatchNorm1d(332, eps=1e-05, momentum=0.1, affine=True)
    (act_func): ReLU()
  )
  (5): Layer1d(
    (layer): Linear(in_features=332, out_features=1, bias=True)
  )
)

### Scheduled random model

1. Create first layer with random parameters
2. Next layer's parameters dependent on the previous one

In [2]:
from math import ceil
from random import uniform
from torch.nn import ReLU

g = Generator1d(290, 1,
                n_neuron=[ceil(uniform(0.8, 1.2) * 290) for n in range(5)],
                act_func=(ReLU(),),
                drop_out=(0.1,),
                batch_normalize=(wrap.L1.batch_norm(), wrap.L1.batch_norm(momentum=0.2))
               )
N_MAX = 20
def scheduler(i, paras):
    print('layer %s' % i)
    n_out = max(ceil(paras['n_out'] * uniform(0.5, 0.8)), N_MAX)
    return dict(paras, n_out=n_out)

ms = g(5, n_models=10,
       replace=True,
       scheduler=scheduler
       )
m = next(ms)
m
# len(list(m))

layer 1
layer 2
layer 3
layer 4


Sequential(
  (0): Layer1d(
    (layer): Linear(in_features=290, out_features=253, bias=True)
    (batch_nor): BatchNorm1d(253, eps=1e-05, momentum=0.2, affine=True)
    (act_func): ReLU()
    (dropout): Dropout(p=0.1)
  )
  (1): Layer1d(
    (layer): Linear(in_features=253, out_features=127, bias=True)
    (batch_nor): BatchNorm1d(127, eps=1e-05, momentum=0.2, affine=True)
    (act_func): ReLU()
    (dropout): Dropout(p=0.1)
  )
  (2): Layer1d(
    (layer): Linear(in_features=127, out_features=79, bias=True)
    (batch_nor): BatchNorm1d(79, eps=1e-05, momentum=0.2, affine=True)
    (act_func): ReLU()
    (dropout): Dropout(p=0.1)
  )
  (3): Layer1d(
    (layer): Linear(in_features=79, out_features=40, bias=True)
    (batch_nor): BatchNorm1d(40, eps=1e-05, momentum=0.2, affine=True)
    (act_func): ReLU()
    (dropout): Dropout(p=0.1)
  )
  (4): Layer1d(
    (layer): Linear(in_features=40, out_features=22, bias=True)
    (batch_nor): BatchNorm1d(22, eps=1e-05, momentum=0.2, affine=True

### Train model by using elemental descriptors with property density

1. Use `xenonpy.model.nn.ModelRunner` to train model.
2. Draw a scatter grahp with y_test and y_true.

In [3]:
from sklearn.preprocessing import minmax_scale, StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from scipy.stats import boxcox

from xenonpy.utils.datatools import Loader, Saver
from xenonpy.visualization import DescHeatmap
import numpy as np

# Saver
save = Saver('dens_predict')

# load descriptors and property
# If your got FileNotFoundError
# run samples/calculate_elemental_descriptors.ipynb first
loader = Loader()
dens = loader('density').last()
desc_dens = loader('dens_desc').last()

# box-cox transfer
dens_bc, lmd = boxcox(dens - dens.min() + 1E-6)
save(dens_bc=dens_bc, lmd=lmd)

# standarded descriptor
scaler = StandardScaler()
desc_dens_scale = scaler.fit_transform(desc_dens)
save(desc_dens_scale=desc_dens_scale, scale_mean=scaler.mean_, scale=scaler.scale_)

In [4]:
%%time
import torch

from xenonpy.model.nn import ModelRunner
from xenonpy.model.nn.wrap import Optim, Init
from sklearn.metrics import mean_absolute_error
from sklearn.model_selection import train_test_split

# split dataset
X_train, X_test, y_train, y_test = train_test_split(desc_dens_scale, dens_bc, test_size=0.2, random_state=0)

with ModelRunner(3000, log_step=300, check_step=300, ctx='gpu') as runner:
    runner(m, init_weight=Init.uniform(), loss_func=torch.nn.MSELoss(), optim=Optim.adam(), lr=0.001)
    runner.fit(X_train, y_train)
    y_true, y_pred = runner.predict(X_test, y_test)
    y_true_fit, y_pred_fit = runner.predict(X_train, y_train)
    
mae = mean_absolute_error(y_true, y_pred)
print('Mean absolute error: %s' % mae)

Runner environment:
Running dir: None
Epochs: 3000
Context: GPU
Check step: 300
Log step: 300

init weight -> Linear(in_features=290, out_features=253, bias=True)
init weight -> Linear(in_features=253, out_features=127, bias=True)
init weight -> Linear(in_features=127, out_features=79, bias=True)
init weight -> Linear(in_features=79, out_features=40, bias=True)
init weight -> Linear(in_features=40, out_features=22, bias=True)
init weight -> Linear(in_features=22, out_features=1, bias=True)
=======start training=======
Model name: fbe7efd4ed3401f7cda1b72b307ac06d

at step[0/3000], Loss=3.9353
at step[300/3000], Loss=0.0374
at step[600/3000], Loss=0.0282
at step[900/3000], Loss=0.0247
at step[1200/3000], Loss=0.0220
at step[1500/3000], Loss=0.0200
at step[1800/3000], Loss=0.0176
at step[2100/3000], Loss=0.0156
at step[2400/3000], Loss=0.0145
at step[2700/3000], Loss=0.0101

Final loss=0.0081
=======over training=======

Mean absolute error: 0.08830138854873626
Wall time: 1min 38s


In [5]:
# save
save(y_true=y_true, y_pred=y_pred, y_true_fit=y_true_fit, y_pred_fit=y_pred_fit, model=m)

In [6]:
from plotly.offline import iplot, init_notebook_mode
from scipy.special import inv_boxcox
from plotly.graph_objs import Scattergl

y_true = loader('dens_predict').last('y_true')
y_pred = loader('dens_predict').last('y_pred')
y_true_fit = loader('dens_predict').last('y_true_fit')
y_pred_fit = loader('dens_predict').last('y_pred_fit')

y_true = inv_boxcox(y_true, lmd)
y_pred = inv_boxcox(y_pred, lmd)
y_true_fit = inv_boxcox(y_true_fit, lmd)
y_pred_fit = inv_boxcox(y_pred_fit, lmd)

data = [
    Scattergl(
        x=y_true_fit,
        y=y_pred_fit,
        name='train',
        mode='markers',
        marker=dict(
            opacity=0.5,
            size=8
        )
    ),
    Scattergl(
        x=y_true,
        y=y_pred,
        name='test',
        mode='markers',
        marker=dict(
            opacity=0.5,
            size=8
        )
    )]

init_notebook_mode()
iplot(data)

